In [1]:
import altair as alt
import pandas as pd
import streamlit as st

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
# Conjunto completo de datos
covid_data=pd.read_csv("https://raw.githubusercontent.com/govex/COVID-19/master/data_tables/vaccine_data/global_data/time_series_covid19_vaccine_global.csv")
# Agrupamos por región y fecha
grouped_data=covid_data.groupby(['Country_Region','Date']).sum()
# Convertimos índices en columnas 
data=grouped_data.reset_index()
# Cambiamos el tipo de datoos a fecha
data['Date']=data['Date'].astype('datetime64[ns]')


In [3]:
# Obtenemos la población mundial por paises para poder obtener porcentajes
population=pd.read_csv("../data/population_by_country_2020.csv")

# Hacemos un left join entre los datos de porcentaje de vacunación y población
data=data.join(
    population[["Country (or dependency)", "Population (2020)"]].set_index(
        "Country (or dependency)"
    ),
    on="Country_Region",
)

# Obtenemos los porcentajes
data['Doses_admin_pct']=data['Doses_admin']/data['Population (2020)']
data['People_partially_vaccinated_pct']=data['People_partially_vaccinated']/data['Population (2020)']
data['People_fully_vaccinated_pct']=data['People_fully_vaccinated']/data['Population (2020)']
data.head(1)

Country_Region       Date  Doses_admin  People_partially_vaccinated  \
0    Afghanistan 2021-02-22            0                          0.0   

   People_fully_vaccinated  UID  Population (2020)  Doses_admin_pct  \
0                      0.0  4.0         39074280.0              0.0   

   People_partially_vaccinated_pct  People_fully_vaccinated_pct  
0                              0.0                          0.0

In [8]:
# Crear gráfica Altair (for the win)
input_dropdown = alt.binding_select(options=sorted(list(set(data["Country_Region"]))))
selection = alt.selection_single(
    fields=["Country_Region"], bind=input_dropdown, name="Pais"
)

chart = (
    alt.Chart(data)
    .mark_line()
    .encode(
        x="Date:T",
        color="Country_Region",
        strokeDash="Country_Region",
        tooltip=[
            "Country_Region",
            "Date",
            "People_fully_vaccinated_pct",
            "Doses_admin_pct",
            "Doses_admin",
            "Population (2020)",
        ],
    )
    .add_selection(selection)
    .transform_filter(selection)
    .properties(width=660)
)

chart.encode(y="People_fully_vaccinated_pct:Q").interactive()

alt.Chart(...)